In [1]:
import pandas as pd
import numpy as np
import geopandas as gpd
import matplotlib.pyplot as plt
from pathlib import Path
from shapely.geometry import box, Point, Polygon
import xarray as xr
import rioxarray
from rasterio.features import shapes
import os
import folium
from geocube.api.core import make_geocube
from src.utils import read_neon_trees

root = Path.cwd()

In [11]:
site_name = 'harv'
epsg = 26918
date = '2018'


species_colname = 'taxonID'
beech_code = 'FAGR'
dbh_column = 'dbh_inches'

# trees = read_neon_trees(root, 'BART', 26919) 
# trees['dbh_inches'] = trees['stemDiameter']/2.54
#trees = gpd.read_file(root / 'output' /'BART'/'all_trees_BART.gpkg')
#trees = trees[trees['taxonID']!='2PLANT'] # remove unidentified tree

trees = gpd.read_file(root / 'output' / site_name.upper() / 'filtered_trees_HARV.gpkg')
trees = trees.to_crs(epsg)

In [13]:

def trees_to_sentinel_grid(tree_points,date, site_name,epsg):
        # read in sentinel
        r = xr.open_dataarray(root /'sentinel_data' / site_name / f'{date}_{site_name}.nc')
        r = r.rio.write_crs(epsg).rio.set_spatial_dims(x_dim="x",y_dim="y",).rio.write_coordinate_system()
        r = r.isel(band=0,time=0)

        # vectorize raster
        r1_unique = np.arange(r.size).reshape(r.shape) 
        r1_unique = r1_unique.astype('uint16') 
        r1 = xr.DataArray(r1_unique, coords={'y': r.y.values, 'x': r.x.values},dims=['y','x'])
        r1 = r1.rio.write_crs(epsg).rio.set_spatial_dims(x_dim="x",y_dim="y",).rio.write_coordinate_system()
        polygons = shapes(r1_unique, transform=r1.rio.transform()) # returns (geojson, value) for each raster grid cell

        #Create a list of polygon geojsons
        geometry = [Polygon(polygon['coordinates'][0])for polygon, _ in polygons]

        # Create a GeoDataFrame from the features
        gdf_dict = {'geometry':geometry,'cell_id':list(range(1,len(geometry)+1))}

        gdf = gpd.GeoDataFrame(gdf_dict, crs=r1.rio.crs)

        # join tree points to polygons
        j = gpd.sjoin(gdf, tree_points, predicate='contains')

        return j



In [9]:
j.shape

(1897, 15)

In [ ]:
bart_tree_dict = {'TSCA':'hemlock','FAGR': 'beech','ACRU': 'maple','BEAL2':'birch','PIRU':'spruce','ACSAS':'maple','BEPAP': 'birch','FRAM2': 'ash','ACPE': 'maple','POGR4': 'aspen', 'POTR5' : 'aspen', 'BEPAC2': 'birch', 'ABBA' : 'balsam_fir','BECAC':'birch','BEPO':'birch', 'PIST': 'pine', 'PIRE': 'pine', 'FRPE': 'ash', 'ULAM': 'elm', 'QURU': 'oak', 'TIAM': 'basswood', 'OSVI': 'ironwood', 'PRPE':'cherry'}

# add genus column based on tree code
j['genus'] = j['taxonID'].apply(lambda x: tree_dict.get(x))
# drop unneeded columns
j = j.drop(['index_right', 'Unnamed: 0', 'plotID',
       'individualID', 'easting_tree', 'northing_tree','adjCoordinateUncertainty', 'utmZone', 'easting_plot', 'northing_plot'],axis=1)
# dbh in inches gives basal area in sqare feet
j['basal_area'] = .005454 * j[dbh_column]**2

# seperate basal area into column for each genus
for value in tree_dict.values():
    j[f'{value}_basal_area'] = j.apply(lambda row: row['basal_area'] if row['genus']==value else 0, axis=1)


# aggregate basal area by cell/pixel
j2 = j.groupby('cell_id').agg({'basal_area': 'sum', 'taxonID': 'count'}).rename(columns={'taxonID': 'num_trees'}).reset_index()
for genus in j.genus.unique():
    if genus is not None:
        j1 = j.groupby('cell_id').agg({f'{genus}_basal_area':'sum'}).reset_index()
        j2 = pd.merge(j2,j1,on='cell_id',how='left')


# merge with geometry
merged = gdf.merge(j2, on='cell_id', how='inner')

# convert to percent basal area
for genus in j.genus.unique():
    if genus is not None:
        merged[f'{genus}_basal_area'] = (merged[f'{genus}_basal_area']/merged['basal_area'])*100


In [12]:
all_ba = xr.Dataset()
# add category column based on species makeup of pixel
all_species = ['beech','hemlock','maple','birch','spruce'] 
for i in range(len(all_species)):
    target_species = all_species[i]
    nontarget_species = [x for x in all_species if x != target_species] 

    categories = [0,1,2,3,4,5,6]
    category_labels = [f'0% {target_species}',f'100% {target_species}',f'mixed {target_species}',f'mixed {nontarget_species[0]}',
                f'mixed {nontarget_species[1]}',f'mixed {nontarget_species[2]}', f'mixed {nontarget_species[3]}','mixed - other']
    label_df = pd.DataFrame({'cat_numbers':[0,1,2,3,4,5,6,7],'cat_labels':category_labels})
    label_df.to_csv(root / 'output' / 'BART' / f'{target_species}_category_labels.csv') # save labels for reference

    conditions = [merged[f'{target_species}_basal_area']==0.0,
                merged[f'{target_species}_basal_area']==100.0,
                ((merged[f'{target_species}_basal_area']>=50)&(merged[f'{target_species}_basal_area']<100)),
                ((merged[f'{nontarget_species[0]}_basal_area']>=50)&(merged[f'{nontarget_species[0]}_basal_area']<100)),
                ((merged[f'{nontarget_species[1]}_basal_area']>=50)&(merged[f'{nontarget_species[1]}_basal_area']<100)),
                ((merged[f'{nontarget_species[2]}_basal_area']>=50)&(merged[f'{nontarget_species[2]}_basal_area']<100)),
                ((merged[f'{nontarget_species[3]}_basal_area']>=50)&(merged[f'{nontarget_species[3]}_basal_area']<100)),
                ]

    merged[f'{target_species}_category'] = np.select(conditions,categories,default=7)

    #remove cells with only one target tree
    merged = merged.loc[~((merged[f'{target_species}_basal_area']==100.0)&(merged['num_trees']==1))] 

    # convert to raster
    ba = make_geocube(
    vector_data=merged,
    measurements=[f"{target_species}_basal_area",f"{target_species}_category"],
    like=r1, # ensure the data are on the same grid
    )

    all_ba[f"{target_species}_basal_area"] = ba[f"{target_species}_basal_area"]
    all_ba[f"{target_species}_category"] = ba[f"{target_species}_category"]




In [13]:
all_ba.to_netcdf(root / 'output' / 'BART' / f'basal_area_BART.nc')

In [10]:
# check vectorization of raster

cc = tuple(trees.to_crs(4326).geometry.get_coordinates().iloc[0,:])[::-1]
m = folium.Map(location= cc, zoom_start=11)



folium.GeoJson(
    j.to_crs(4326)
).add_to(m)

folium.GeoJson(
    trees.to_crs(4326),
    marker=folium.Circle(radius=2, fill_color="orange", fill_opacity=0.4, color="red", weight=1)
).add_to(m)

m
